# REDO AGE, MASS PLOTS

# Read in all the files, and make some plots

*Andrew Bowen provided some of the script to read in the file. [See his GitHub repo](https://github.com/andrewbowen19/CEB_Project)*

Some alterations to files:
- changed Pismis 6 to NGC 2645 in MWSC, Piskunov and Kharchenko
- Luginbuhl-Skiff_1 is Skiff_J0614+12.9 (?) changed in WEBDA
- Skiff_2 is Skiff_J0458+43.0 (?) changed in WEBDA
- PTB 9 is a planetary nebula (not an OC --though maybe in the OC NGC 7762?) -- changed label in MWSC, removed from Kharchenko
- Collinder_258 is Harvard_5 (same PM, distance, etc.), both are in Gaia table, removed Harvard_5
- FSR_1686 is Juchert_10, changed to Juchert 10 in MWSC and Kharchenko
- changed many BH or VBH, etc. to vdBergh-Hagen
- removed Berkeley 42 from vandenbergh and Salaris because it's a GC (and included in Harris)
- removed Mrk 38 from vandenbergh because it's a pair of galaxies
- removed Mrk 50 from vandenbergh because it's a Seyfert 1 galaxy
- vdBergh-Hagen_133 is Collinder_258 is Harvard 5,removed vdBergh-Hagen 133 in lynga
- Berkeley_30 is Biurakan_9, changed to Berkeley 30 in lynga
- Berkeley_32 Biurakan_8, changed to Berkeley 32 in lynga
- removed NGC 281 from lunga (HII region)
- not sure about NGC_2579 and AH03_J0822-36.4 (possible overlap)
- removed vdBergh-Hagen_1 from vandenberg = reflection nebula
- Cl VDBH 47 is IC 2395, remove vdBergh-Hagen 47 from WEBDA and lynga
- vdBergh-Hagen_218 might be NGC_6318 , removed vdBergh-Hagen_218 from lynga

In [3]:
import pandas as pd
import numpy as np
from scipy.stats import gaussian_kde
import sys
import time
import re

from astropy.coordinates import SkyCoord
from astropy import units 

from astroquery.simbad import Simbad
Simbad.TIMEOUT = 300 # sets the timeout to 60s

import warnings
warnings.filterwarnings('ignore', category=UserWarning, append=True)

import matplotlib.pyplot as plt

pd.set_option('display.max_columns', 500)
pd.set_option('display.max_rows', 50)

%matplotlib inline

In [4]:
from difflib import SequenceMatcher

def similar(a, b):
    return SequenceMatcher(None, a, b).ratio()

In [17]:
def OLDmatchToSimbad(cat_ID, cat_RA, cat_Dec, gal=False, max_sep = 2.0 * units.arcmin, str_overlap = 0.8, fillCat = True):
    #I'd like to use the Simbad names for matching (if possible) so I reduce the duplicates, 
    #but I need to match to coords also !

    if (gal):
        catalog = SkyCoord(l = cat_RA, b = cat_Dec, frame='galactic').icrs
    else:
        catalog = SkyCoord(ra = cat_RA, dec = cat_Dec, frame='icrs')

    match_ID = np.array([str(x) for x in cat_ID], dtype='object')
    return_ID = np.full(len(match_ID), np.nan, dtype='object')

    #fix the names
    #is this correct? : .replace('vdBergh','CL VDBH')
    for i, x in enumerate(match_ID):
        match_ID[i] = x.replace('vdBergh-Hagen_','Cl_VDBH_')\
                        .replace('vdBergh_','Cl_VDB_')\
                        .replace('FSR_','[FSR2007]_')\
                        .replace('DBSB_','[DBS2003]_')\
                        .replace('BDSB_','[BDS2003]_')\
                        .replace('BDS_','[BDS2003]_')\
                        .replace('Alessi_','Cl_Alessi_')\
                        .replace('Bica_','Cl_Bica_')\
                        .replace('Sher_','Cl_Sher_')\
                        .replace('MWSC_','[KPS2012]_MWSC_')\
                        .replace('Schuster_1','NAME_SCHUSTER_CL')\
                        .replace('ASCC_','[KPR2005]_')\
                        .replace('Andrews-Lindsay_', '[AL67]_Cl*')\
                        .replace('Arp-Madore', 'AM')\
                        .replace('LDN_988e', 'NAME_[C86]_L988_e_Cluster')\
                        .replace('Juchert-Saloran_','Juchert-Saloranta_')\
                        .replace('Ivanov', '[IBP2002]_CC')\
                        .replace('DB2001_','[DB2001]_Cl ')\
                        .replace('Cl_Cl','Cl')\
                        .replace('[KPS2012]_[KPS2012]','[KPS2012]')\

#     result_table = Simbad.query_objects(match_ID) #stupidly, this does not return blank rows for missing data!
# below I tried matching by RA and Dec, but I'm finding that (according to authors) there are quite a few 
# unique clusters, that are very close together, and it's not clear how to get avoid mismatches.
# If it returned blank lines, then this wouldn't be an issue!!
# So I'm trying to go one line at a time, but of course Simbad doesn't like that... it rejects my connection when
# I have too many requests (and what is too many?  and how long should I wait?)
    for i, ID in enumerate(match_ID):
        result_table = Simbad.query_object(ID)
        if (result_table):
            #print(result_table)
            if (len(result_table) > 0):
                row = result_table[0]
                newID =  re.sub('\s+', ' ', row['MAIN_ID'].decode("utf-8")).strip().replace(' ','_' )
                return_ID[i] = newID
        print(f'{i} {float(i)/len(match_ID):5.3f}, {ID} {return_ID[i]} -- ', end='')
        if (i>0 and i % 50 == 0):
            time.sleep(30)
            print('\n\n')
        time.sleep(0.2)


#     #print(result_table)
    
#     dist = [max_sep for x in match_ID]
#     for row in result_table:
#         c = SkyCoord(ra = row['RA'] + ' hour', dec = row['DEC'] + ' degree', frame='icrs')
#         idx, d2d, d3d = c.match_to_catalog_sky(catalog, nthneighbor=1)
#         newID =  re.sub('\s+', ' ', row['MAIN_ID'].decode("utf-8")).strip().replace(' ','_' )
#         if(~pd.isna(match_ID[idx])): #take only the nearest one (in case there are multiple matches)
#             if (d2d < dist[idx] or similar(newID, match_ID[idx]) > str_overlap):
#                 dist[idx] = d2d
#                 return_ID[idx] = newID

    #search by coordinates? no because I can't get the type of object from this query
    for i, ID in enumerate(return_ID):
        #print(ID)
        #if (pd.isna(ID)):
        #    print('No Simbad match', match_ID[i], ID)
        #    return_table = Simbad.query_region(catalog[i], radius=max_sep)
        #    return_table.pprint_all()
            
        if (pd.isna(ID) and fillCat):
            return_ID[i] = match_ID[i]
        
    return return_ID

In [22]:
def matchToSimbad(cat_ID, fillCat = True):
    #I'd like to use the Simbad names for matching (if possible) so I reduce the duplicates, 

    match_ID = np.array([str(x) for x in cat_ID], dtype='object')
    return_ID = np.full(len(match_ID), np.nan, dtype='object')

    #fix the names
    #is this correct? : .replace('vdBergh','CL VDBH')
    for i, x in enumerate(match_ID):
        match_ID[i] = x.replace('vdBergh-Hagen_','Cl_VDBH_')\
                        .replace('vdBergh_','Cl_VDB_')\
                        .replace('FSR_','[FSR2007]_')\
                        .replace('DBSB_','[DBS2003]_')\
                        .replace('BDSB_','[BDS2003]_')\
                        .replace('BDS_','[BDS2003]_')\
                        .replace('Alessi_','Cl_Alessi_')\
                        .replace('Bica_','Cl_Bica_')\
                        .replace('Sher_','Cl_Sher_')\
                        .replace('MWSC_','[KPS2012]_MWSC_')\
                        .replace('Schuster_1','NAME_SCHUSTER_CL')\
                        .replace('ASCC_','[KPR2005]_')\
                        .replace('Andrews-Lindsay_', '[AL67]_Cl*')\
                        .replace('Arp-Madore', 'AM')\
                        .replace('LDN_988e', 'NAME_[C86]_L988_e_Cluster')\
                        .replace('Juchert-Saloran_','Juchert-Saloranta_')\
                        .replace('Ivanov', '[IBP2002]_CC')\
                        .replace('DB2001_','[DB2001]_Cl ')\
                        .replace('Cl_Cl','Cl')\
                        .replace('[KPS2012]_[KPS2012]','[KPS2012]')\

#     result_table = Simbad.query_objects(match_ID) #stupidly, this does not return blank rows for missing data!
# below I tried matching by RA and Dec, but I'm finding that (according to authors) there are quite a few 
# unique clusters, that are very close together, and it's not clear how to get avoid mismatches.
# If it returned blank lines, then this wouldn't be an issue!!
# So I'm trying to go one line at a time, but of course Simbad doesn't like that... it rejects my connection when
# I have too many requests (and what is too many?  and how long should I wait?)
    for i, ID in enumerate(match_ID):
        result_table = Simbad.query_object(ID)
        if (result_table):
            #print(result_table)
            if (len(result_table) > 0):
                row = result_table[0]
                newID =  re.sub('\s+', ' ', row['MAIN_ID'].decode("utf-8")).strip().replace(' ','_' )
                return_ID[i] = newID
        print(f'{i} {float(i)/len(match_ID):5.3f}, {ID} {return_ID[i]} -- ', end='')
        if (i>0 and i % 100 == 0):
            time.sleep(30)
            print('\n\n')
        time.sleep(0.2)

    #fill nans with the original catalog search input?
    if (fillCat):
        for i, ID in enumerate(return_ID):
            if (pd.isna(ID)):
                return_ID[i] = match_ID[i]
        
    return return_ID

In [18]:
fixMWSC = True
fixWEBDA = True
fixPiskunov = True
fixKharchenko = True
fixSalaris = True
fixVandenBergh = True
fixGaia = True
fixLynga = True

In [19]:
#MWSC - Milky Way Star Clusters Catalog
#https://heasarc.gsfc.nasa.gov/W3Browse/all/mwsc.html
if (fixMWSC):
    mwsc_df = pd.read_csv("MWSC.txt", header=3, delimiter='|')
    mwsc_df.columns = mwsc_df.columns.str.strip()

    
    #take only the open clusters
    mwsc_df = mwsc_df.loc[(~mwsc_df['class'].str.strip().str.contains('GLOBULAR')) &
                          (~mwsc_df['class'].str.strip().str.contains('NEBULA')) &
                          (~mwsc_df['class'].str.strip().str.contains('UNIDENTIFIED'))]

    #remove the "Unnamed" columns
    mwsc_df = mwsc_df.loc[:, ~mwsc_df.columns.str.contains('^Unnamed')]

    print(set(mwsc_df['class'].values))
    
    #fix the IDs
    mwsc_ID = mwsc_df['Name']
    mwsc_ID = mwsc_ID.str.strip().str.replace( ' ','_' )
    mwsc_df['Name'] = mwsc_ID

    #add Simbad names for matching (if possible) so I reduce the duplicates 
    RA = [x + ' hour' for x in mwsc_df['ra']]
    Dec = [x + 'degree' for x in mwsc_df['dec']]
    ID = [x for x in mwsc_df['Name']]
    simbad_ID = matchToSimbad(mwsc_ID, RA, Dec)
    
    mwsc_df.insert(loc=0, column='Simbad_ID', value=simbad_ID)

    #check for duplicates
    for index, row in  mwsc_df.iterrows():
        check = mwsc_df.loc[mwsc_df['Simbad_ID'] == row['Simbad_ID']]
        if (len(check['Simbad_ID']) != 1):
            print('MWSC', row['Simbad_ID'], row['Name'])
            print('Check', check['Simbad_ID'].values, len(check['Simbad_ID']))
            print('')
        
    mwsc_df.to_csv('MWSC_clean.csv', index=False)
    

mwsc_df = pd.read_csv('MWSC_clean.csv')
mwsc_df

{'                                  OPEN STAR CLUSTER', '                          OB ASSOCIATION/HII REGION'}


0 0.000, [KPS2012]_MWSC_4688 [KPS2012]_MWSC_4688 -- 1 0.000, [KPS2012]_MWSC_5684 nan -- 2 0.001, [KPS2012]_MWSC_5692 nan -- 3 0.001, [KPS2012]_MWSC_4005 [KPS2012]_MWSC_4005 -- 4 0.001, [KPS2012]_MWSC_4176 [KPS2012]_MWSC_4176 -- 5 0.002, ESO_008-06 ESO_8-6 -- 6 0.002, [KPS2012]_MWSC_4219 [KPS2012]_MWSC_4219 -- 7 0.002, [KPS2012]_MWSC_5575 nan -- 8 0.003, [KPS2012]_MWSC_4682 [KPS2012]_MWSC_4682 -- 9 0.003, [KPS2012]_MWSC_5685 nan -- 10 0.003, [KPS2012]_MWSC_5681 nan -- 11 0.004, [FSR2007]_1626 [KPS2012]_MWSC_2014 -- 12 0.004, [FSR2007]_1631 [KPS2012]_MWSC_2064 -- 13 0.004, [FSR2007]_1629 [KPS2012]_MWSC_2049 -- 14 0.005, [KPS2012]_MWSC_5688 nan -- 15 0.005, ESO_026-02 ESO_26-2 -- 16 0.006, [KPS2012]_MWSC_4137 [KPS2012]_MWSC_4137 -- 17 0.006, Melotte_227 Cl_Melotte_227 -- 18 0.006, [KPS2012]_MWSC_5679 nan -- 19 0.007, [KPS2012]_MWSC_5572 nan -- 20 0.007, [KPS2012]_MWSC_5749 nan -- 21 0.007, ESO_021-06 ESO_21-6 -- 22 0.008, [KPS2012]_MWSC_5672 nan -- 23 0.008, [KPS2012]_MWSC_4114 [KPS2012]_

209 0.072, Loden_1101 nan -- 210 0.072, ESO_137-43 ESO_137-43 -- 211 0.073, Kronberger_39 Kronberger_39 -- 212 0.073, ESO_137-23 ESO_137-23 -- 213 0.073, Bochum_12 C_1055-614 -- 214 0.074, Loden_1409 nan -- 215 0.074, Ruprecht_92 Cl_Ruprecht_92 -- 216 0.074, [DBS2003]_77 [DBS2003]_77 -- 217 0.075, NGC_3766 NGC_3766 -- 218 0.075, Trumpler_11 C_1003-613 -- 219 0.075, [DBS2003]_80 [DBS2003]_80 -- 220 0.076, Ruprecht_105 Cl_Ruprecht_105 -- 221 0.076, [FSR2007]_1668 [KPS2012]_MWSC_2180 -- 222 0.076, [DBS2003]_66 [DBS2003]_66 -- 223 0.077, Cl_VDBH_110 C_1105-612 -- 224 0.077, [FSR2007]_1666 [KPS2012]_MWSC_2167 -- 225 0.077, Loden_1256 nan -- 226 0.078, Ruprecht_93 Cl_Ruprecht_93 -- 227 0.078, Hogg_17 Cl_Hogg_17 -- 228 0.078, Collinder_272 Cl_Collinder_272 -- 229 0.079, Lynga_2 Cl_Lynga_2 -- 230 0.079, [DBS2003]_62 [DBS2003]_62 -- 231 0.079, Loden_481 nan -- 232 0.080, Ruprecht_161 C_1007-609 -- 233 0.080, Shorlin_2 nan -- 234 0.080, NGC_4103 NGC_4103 -- 235 0.081, Shorlin_1 NAME_Shorlin_1 --

428 0.147, [DBS2003]_125 [DBS2003]_125 -- 429 0.148, IC_2488 IC_2488 -- 430 0.148, [FSR2007]_1701 [KPS2012]_MWSC_2296 -- 431 0.148, Turner_7 Cl_Turner_7 -- 432 0.149, ESO_175-06 ESO_175-6 -- 433 0.149, Ruprecht_114 C_1602-567 -- 434 0.149, [KPR2005]_61 [KPR2005]_61 -- 435 0.150, [FSR2007]_1569 [KPS2012]_MWSC_1935 -- 436 0.150, [FSR2007]_1602 [KPS2012]_MWSC_2008 -- 437 0.150, Loden_89 nan -- 438 0.151, Loden_112 nan -- 439 0.151, [DBS2003]_93 [DBS2003]_93 -- 440 0.151, Lynga_5 Cl_Lynga_5 -- 441 0.152, [FSR2007]_1521 [FSR2007]_1521 -- 442 0.152, NGC_5662 NGC_5662 -- 443 0.152, Loden_27 nan -- 444 0.153, Cl_VDBH_78 C_0942-563 -- 445 0.153, [FSR2007]_1697 [KPS2012]_MWSC_2274 -- 446 0.153, NGC_5999 NGC_5999 -- 447 0.154, Basel_20 C_0931-561 -- 448 0.154, Ruprecht_165 C_1225-561 -- 449 0.154, NGC_3033 NGC_3033 -- 450 0.155, Cl_VDBH_92 Cl_VDBH_92 -- 451 0.155, Loden_189 nan -- 452 0.155, [DBS2003]_141 [DBS2003]_141 -- 453 0.156, [FSR2007]_1648 [KPS2012]_MWSC_2109 -- 454 0.156, Ruprecht_75 C_0

ConnectionError: ('Connection aborted.', RemoteDisconnected('Remote end closed connection without response'))

### Downloaded from WEBDA [here](https://webda.physics.muni.cz/cluster_selall.html)

With RA from 0 to 24 and 0 to 1e6 stars. I copied the table to WEBDA.html, and removed the $<$br$>$ entries, then converted to csv with 

https://codepen.io/malahovks/pen/gLxLWX

or

https://jsfiddle.net/gengns/j1jm2tjx/

Finally, I separated the RA and DEC column header into 2 entries.

*I also have a data file from David James, that has more clusters, but I'm not sure the providence of that, so I won't use it.*

In [27]:
# # WEBDA data file (2013)
# webda_df = pd.read_fwf("WEBDA-OC-table-June2013_DavidJames.txt", 
#                        widths = [18,14,15,11,9,8,8,8,9,6,9,9,9,7,7,9], header = 0)

if (fixWEBDA):
    webda_df = pd.read_csv('WEBDA.csv')
    #fix the IDs
    webda_ID = webda_df['Name']
    webda_ID = webda_ID.str.replace( 'NGC 0','NGC ' ).str.replace( ' ','_' )

    webda_df['Name'] = webda_ID

    #add Simbad names for matching (if possible) so I reduce the duplicates 
    RA = [x + ' hour' for x in webda_df['RA_2000']]
    Dec = [x + 'degree' for x in webda_df['Dec_2000']]
    simbad_ID = matchToSimbad(webda_ID, RA, Dec)
    webda_df.insert(loc=0, column='Simbad_ID', value=simbad_ID)
        
    #check for duplicates  
    for index, row in  webda_df.iterrows():
        check = webda_df.loc[webda_df['Simbad_ID'] == row['Simbad_ID']]
        if (len(check['Simbad_ID']) != 1):
            print('WEBDA', row['Simbad_ID'], row['Name'])
            print('Check', check['Simbad_ID'].values, len(check['Simbad_ID']))
            print('')
        
    webda_df.to_csv('WEBDA_clean.csv', index=False)
    
webda_df = pd.read_csv('WEBDA_clean.csv')
webda_df

Simbad_ID              Name   RA_2000   Dec_2000        l  \
0             Cl_Berkeley_58       Berkeley_58  00 00 12  +60 58 00  116.753   
1                Cl_Stock_18          Stock_18  00 01 37  +64 37 30  117.624   
2             Cl_Berkeley_59       Berkeley_59  00 02 13  +67 25 11  118.220   
3                Cl_Blanco_1          Blanco_1  00 04 07  -29 50 00   15.572   
4                [KPR2005]_1            ASCC_1  00 09 35  +62 40 48  118.150   
5              Cl_Berkeley_1        Berkeley_1  00 09 36  +60 28 30  117.796   
6                 C_0007+609           King_13  00 10 06  +61 10 00  117.968   
7               [KPR2004b]_4         Alessi_20  00 10 33  +58 45 35  117.640   
8                [KPR2005]_2            ASCC_2  00 19 51  +55 42 35  118.460   
9            NAME_Cl_Mayer_1           Mayer_1  00 21 54  +61 44 24  119.440   
10                C_0019+641            King_1  00 22 04  +64 22 50  119.763   
11               Cl_Stock_20          Stock_20  00 25 15  +62 37 11  119.920   
12                   NGC_103           NGC_103  00 25 16  +61 19 24  119.797   
13                C_0027+577          Stock_21  00 29 49  +57 55 11  120.050   
14                   NGC_129           NGC_129  00 30 00  +60 13 06  120.270   
15               [KPR2005]_3            ASCC_3  00 31 08  +55 16 47  120.020   
16                   NGC_133           NGC_133  00 31 19  +63 21 00  120.678   
17                   NGC_136           NGC_136  00 31 31  +61 30 36  120.558   
18                C_0029+628           King_14  00 31 54  +63 10 00  120.729   
19                   NGC_146           NGC_146  00 33 03  +63 18 06  120.868   
20                   NGC_189           NGC_189  00 39 35  +61 05 06  121.499   
21                 Cl_Dias_1            Dias_1  00 42 35  +64 04 05  121.964   
22                   NGC_225           NGC_225  00 43 39  +61 46 30  122.011   
23                C_0040+598         Czernik_2  00 43 42  +60 09 00  121.968   
24                C_0040+639           King_16  00 43 45  +64 11 08  122.095   
25             Cl_Berkeley_4        Berkeley_4  00 45 01  +64 23 05  122.238   
26                   NGC_188           NGC_188  00 47 28  +85 15 18  122.843   
27            Cl_Berkeley_61       Berkeley_61  00 48 30  +67 12 00  122.647   
28                   IC_1590           IC_1590  00 52 48  +56 37 00  123.123   
29               [KPR2005]_4            ASCC_4  00 53 09  +61 34 48  123.130   
30               Cl_Alessi_1          Alessi_1  00 53 27  +49 34 11  123.260   
31               [KPR2005]_5            ASCC_5  00 57 57  +55 50 24  123.850   
32            Cl_Berkeley_62       Berkeley_62  01 01 00  +63 57 00  123.982   
33                   NGC_381           NGC_381  01 08 19  +61 35 00  124.939   
34                 Platais_2         Platais_2  01 13 01  +32 04 48  128.230   
35                   NGC_433           NGC_433  01 15 11  +60 07 36  125.888   
36                   NGC_436           NGC_436  01 15 58  +58 48 42  126.111   
37                   NGC_457           NGC_457  01 19 35  +58 17 12  126.635   
38                   NGC_559           NGC_559  01 29 31  +63 18 24  127.193   
39                     M_103           NGC_581  01 33 23  +60 39 00  128.053   
40                C_0132+610        Trumpler_1  01 35 42  +61 17 00  128.224   
41                   NGC_637           NGC_637  01 43 04  +64 02 24  128.546   
42                   NGC_654           NGC_654  01 44 00  +61 53 06  129.082   
43                   NGC_659           NGC_659  01 44 24  +60 40 24  129.375   
44                   NGC_663           NGC_663  01 46 09  +61 14 06  129.467   
45               [KPR2005]_6            ASCC_6  01 47 13  +57 43 47  130.340   
46             Collinder_463     Collinder_463  01 48 24  +71 57 00  127.192   
47              Collinder_21      Collinder_21  01 50 11  +27 04 00  138.733   
48             Cl_Berkeley_6        Berkeley_6  01 51 12  +61 05 00  130.094   
49                 

In [28]:
#Piskunov (2008)
if (fixPiskunov):
    piskunov_df = pd.read_fwf("Piskunov2008.table", 
                              widths = [6,18,7,7,8,6,6,6,6,6,9,9,6,6,9,9], header = None,
                              names = ['COCD','Name','GLON[deg]','GLAT[deg]','DistMod','E(B-V)','Dist[pc]',\
                                       'logt[yr]','rt[pc]','e_rt[pc]','logM[MSun]','e_logM[MSun]','rtA[pc]','e_rtA[pc]',
                                       'logMA[MSun]','e_logMA[MSun]'])

    piskunov_df.replace(-9.999,np.nan, inplace=True)
    piskunov_df.replace(-9.9,np.nan, inplace=True)

    #fix the IDs
    piskunov_ID = piskunov_df['Name']
    piskunov_ID = piskunov_ID.str.strip().str.replace(' ','_' )
    piskunov_df['Name'] = piskunov_ID
    
    #add Simbad names for matching (if possible) so I reduce the duplicates 
    l = [x*units.degree for x in piskunov_df['GLON[deg]']]
    b = [x*units.degree for x in piskunov_df['GLAT[deg]']]
    simbad_ID = matchToSimbad(piskunov_ID, l, b, gal=True)
    piskunov_df.insert(loc=0, column='Simbad_ID', value=simbad_ID)


    #check for duplicates
    for index, row in piskunov_df.iterrows():
        check = piskunov_df.loc[piskunov_df['Simbad_ID'] == row['Simbad_ID']]
        if (len(check['Simbad_ID']) != 1):
            print('Piskunov', row['Simbad_ID'], row['Name'])
            print('Check', check['Simbad_ID'].values, len(check['Simbad_ID']))
            print('')
        
    piskunov_df.to_csv('Piskunov2008_clean.csv', index=False)

piskunov_df = pd.read_csv('Piskunov2008_clean.csv')
piskunov_df

Simbad_ID  COCD              Name  GLON[deg]  GLAT[deg]  \
0             Cl_Berkeley_58     1       Berkeley_58     116.73      -1.29   
1             Cl_Berkeley_59     2       Berkeley_59     118.22       5.00   
2                Cl_Blanco_1     3          Blanco_1      14.17     -79.02   
3               [KPR2004b]_4     4         Alessi_20     117.64      -3.69   
4            NAME_Cl_Mayer_1     5           Mayer_1     119.44      -0.93   
5                Cl_Stock_20     6          Stock_20     119.92      -0.10   
6                 C_0027+577     7          Stock_21     120.05      -4.83   
7                    NGC_129     8           NGC_129     120.27      -2.54   
8                    NGC_146     9           NGC_146     120.87       0.50   
9                    NGC_225    10           NGC_225     122.01      -1.08   
10             Cl_Berkeley_4    11        Berkeley_4     122.28       1.53   
11                   IC_1590    12           IC_1590     123.12      -6.24   
12               Cl_Alessi_1    13          Alessi_1     123.26     -13.30   
13                   NGC_381    14           NGC_381     124.94      -1.21   
14                 Platais_2    15         Platais_2     128.23     -30.57   
15                   NGC_433    16           NGC_433     125.88      -2.61   
16                   NGC_457    17           NGC_457     126.63      -4.37   
17                     M_103    18           NGC_581     128.05      -1.81   
18                   NGC_637    19           NGC_637     128.54       1.73   
19                   NGC_654    20           NGC_654     129.08      -0.37   
20                   NGC_659    21           NGC_659     129.37      -1.54   
21                   NGC_663    22           NGC_663     129.46      -0.94   
22             Collinder_463    23     Collinder_463     127.28       9.40   
23                C_0149+568    24           Stock_4     131.25      -4.81   
24                   NGC_752    25           NGC_752     137.12     -23.26   
25                   NGC_744    26           NGC_744     132.40      -6.17   
26                   Stock_5    27           Stock_5     130.73       2.60   
27                Cl_Stock_2    28           Stock_2     133.36      -1.92   
28                   NGC_869    29           NGC_869     134.63      -3.72   
29                   NGC_884    30           NGC_884     135.01      -3.60   
30                   NGC_886    31           NGC_886     132.89       2.69   
31                C_0225+604    32           Stock_7     134.66       0.09   
32                   IC_1805    33           IC_1805     134.72       0.91   
33                   NGC_957    34           NGC_957     136.28      -2.65   
34                C_0233+557    35        Trumpler_2     137.37      -3.97   
35                      M_34    36          NGC_1039     143.65     -15.62   
36                  NGC_1027    37          NGC_1027     135.74       1.55   
37                   IC_1848    38           IC_1848     137.19       0.91   
38                C_0255+602    39      Collinder_33     138.09       1.34   
39                Trumpler_3    40        Trumpler_3     138.01       4.50   
40                  Stock_23    41          Stock_23     140.08       2.09   
41             Cl_Melotte_20    42        Melotte_20     147.20      -6.33   
42                C_0324+562    43            King_6     143.35      -0.08   
43              Cl_Alessi_13    44         Alessi_13     237.65     -55.71   
44                  NGC_1342    45          NGC_1342     154.97     -15.38   
45                    IC_348    46            IC_348     160.49     -17.81   
46             Cl_Melotte_22    47        Melotte_22     166.63     -23.47   
47                C_0343+589    48        Tombaugh_5     143.94       3.57   
48                  NGC_1502    49          NGC_1502     143.67       7.65   
49                  NGC_1528    50          NGC_1528     152.05       0.25   
50                  NGC_1545    51       

In [29]:
#Kharchenko (2013)
if (fixKharchenko):
    kharchenko_df = pd.read_fwf("Kharchenko2013.table", 
                              widths = [5,18,2,1,9,8,8,8,7,7,7,7,7,7,8,8,6,6,7,7,8,7,7,7,7,7,7,7,4,8,8,8,8,8,8,5,4,8,7,4], 
                              header = None,
                              names = ['MWSC','Name','Type','n_Type','RA[hr]','Dec[deg]','GLON[deg]','GLAT[deg]',
                                       'r0[deg]','r1[deg]','r2[deg]','pmRA[mas/yr]','pmDec[mas/yr]','e_pm[mas/yr]',
                                       'RV[km/s]','e_RV[km/s]','n_RV[km/s]','N1sr0','N1sr1','N1sr2','d[pc]','E(B-V)',
                                       'appDistMod[mag]','E(J-Ks)','E(J-H)','dH','logt[yr]','e_logt[yr]','Nt','rc[pc]',
                                       'e_rc[pc]','rt[pc]','e_rt[pc]','k[pc-2]','e_k[pc-2]','Src','SType','[Fe/H][Sun]',
                                       'e_[Fe/H][Sun]','n_[Fe/H]'])

    kharchenko_df['RV[km/s]'].replace(999.99,np.nan, inplace=True)
    kharchenko_df['e_RV[km/s]'].replace(99.99,np.nan, inplace=True)
    kharchenko_df['e_logt[yr]'].replace(0.000,np.nan, inplace=True)
    kharchenko_df['Nt'].replace(-1,np.nan, inplace=True)
    kharchenko_df['rc[pc]'].replace(0.00,np.nan, inplace=True)
    kharchenko_df['e_rc[pc]'].replace(0.00,np.nan, inplace=True)
    kharchenko_df['rt[pc]'].replace(0.00,np.nan, inplace=True)
    kharchenko_df['e_rt[pc]'].replace(0.00,np.nan, inplace=True)
    kharchenko_df['k[pc-2]'].replace(0.00,np.nan, inplace=True)
    kharchenko_df['e_k[pc-2]'].replace(0.00,np.nan, inplace=True)
    kharchenko_df['[Fe/H][Sun]'].replace(99.999,np.nan, inplace=True)
    kharchenko_df['e_[Fe/H][Sun]'].replace(9.99,np.nan, inplace=True)
    kharchenko_df['n_[Fe/H]'].replace(0.1,np.nan, inplace=True)

    #kharchenko_df.loc[kharchenko_df['Name'] == 'Skiff_J0458+43.0']
    
    #add Simbad names for matching (if possible) so I reduce the duplicates 
    kharchenko_ID = kharchenko_df['Name']
    RA = [x*units.hourangle for x in kharchenko_df['RA[hr]']]
    Dec = [x*units.degree for x in kharchenko_df['Dec[deg]']]
    simbad_ID = matchToSimbad(kharchenko_ID, RA, Dec)
    kharchenko_df.insert(loc=0, column='Simbad_ID', value=simbad_ID)
    
    kharchenko_df.to_csv('Kharchenko2013_clean.csv', index=False)

kharchenko_df = pd.read_csv('Kharchenko2013_clean.csv')
kharchenko_df

Simbad_ID  MWSC               Name Type  n_Type  \
0                   Cl_Berkeley_58     1        Berkeley_58  NaN     NaN   
1                         NGC_7801     2           NGC_7801  NaN     NaN   
2              [KPS2012]_MWSC_0003     3           FSR_0459  NaN     NaN   
3                      Cl_Stock_18     4           Stock_18  NaN     NaN   
4                   Cl_Berkeley_59     5        Berkeley_59  NaN     NaN   
5                          Cep_OB4     6            Cep_OB4   ao     NaN   
6                      Cl_Blanco_1     7           Blanco_1  NaN     NaN   
7                  Cl_Berkeley_104     8       Berkeley_104  NaN     NaN   
8                  IRAS_00013+6817     9    IRAS_00013+6817  NaN     NaN   
9              [KPS2012]_MWSC_0014    14           FSR_0504  NaN     NaN   
10                          BDB_94    16             BDB_94   rc     NaN   
11                      C_0005+611    17          Czernik_1  NaN     NaN   
12             [KPS2012]_MWSC_0018    18              SAI_1  NaN     NaN   
13                     [KPR2005]_1    19             ASCC_1  NaN     NaN   
14                   Cl_Berkeley_1    20         Berkeley_1  NaN     NaN   
15                      C_0007+609    21            King_13  NaN     NaN   
16                    [KPR2004b]_4    23          Alessi_20  NaN     NaN   
17             [KPS2012]_MWSC_0024    24           FSR_0474  NaN     NaN   
18             [KPS2012]_MWSC_0025    25           FSR_0480  NaN     NaN   
19                           PTB_7    26              PTB_7  NaN     NaN   
20                    [BDS2003]_48    27            BDSB_48   rc     NaN   
21        NAME_Juchert-Saloranta_1    28  Juchert-Saloran_1  NaN     NaN   
22                  Cl_Berkeley_60    29        Berkeley_60  NaN     NaN   
23                     [KPR2005]_2    31             ASCC_2  NaN     NaN   
24                  [FSR2007]_0486    32           FSR_0486  NaN     NaN   
25             [KPS2012]_MWSC_0033    33           FSR_0479  NaN     NaN   
26                 NAME_Cl_Mayer_1    34            Mayer_1  NaN     NaN   
27                      C_0019+641    35             King_1  NaN     NaN   
28             [KPS2012]_MWSC_0036    36           FSR_0477  NaN     NaN   
29             [KPS2012]_MWSC_0037    37              SAI_4  NaN     NaN   
30                         NGC_104    38            NGC_104   go     NaN   
31                     Cl_Stock_20    39           Stock_20  NaN     NaN   
32                         NGC_103    40            NGC_103  NaN     NaN   
33                   Cl_Berkeley_2    41         Berkeley_2  NaN     NaN   
34                  [FSR2007]_0494    42           FSR_0494  NaN     NaN   
35             [KPS2012]_MWSC_0044    44           FSR_0496  NaN     NaN   
36                         NGC_110    45            NGC_110  NaN     NaN   
37             [KPS2012]_MWSC_0046    46              SAI_6  NaN     NaN   
38             [KPS2012]_MWSC_0048    48           FSR_0481  NaN     NaN   
39                  [FSR2007]_0498    50           FSR_0498   rc     NaN   
40             [KPS2012]_MWSC_0051    51           FSR_0503  NaN     NaN   
41                        Stock_21    52           Stock_21  NaN     NaN   
42                         NGC_129    53            NGC_129  NaN     NaN   
43                     [KPR2005]_3    54             ASCC_3   ac     NaN   
44                         NGC_133    55            NGC_133  NaN     NaN   
45                         NGC_136    56            NGC_136  NaN     NaN   
46                      C_0029+628    57            King_14  NaN     NaN   
47                      Cl_King_15    58            King_15  NaN     NaN   
48                         NGC_146    59            NGC_146  NaN     NaN   
49                         NGC_189    62            NGC_189  NaN     NaN   
50                     Cl_Stock_24    63           Stock_24  NaN     NaN   
51                      C_0037+605    65         Dolidze_12  NaN     NaN 

In [30]:
# Salaris (2004) -- no RA or Dec...
if (fixSalaris):
    #salaris_df = pd.read_csv('Salaris2004_viaWEBDA.txt', sep='\t', header = 15)
    salaris_df = pd.read_csv('Salaris2004_table1.txt', sep='\t')
    #print(salaris_df)

    #change the Hyades to Melotte 25 so that it matches with van den Bergh for position
    names = salaris_df['Name'].values
    xx = np.where(names == 'Hyades')
    names[xx] = 'Melotte_25'
    salaris_df['Name'] = [x.strip().replace(' ','_' ) for x in names]
    xx = np.where(names == 'Arp-Madore_2')
    names[xx] = 'AM_2'  

    #no RA and Dec, so can't use the function above
    #this is missing 1 name.  I will look manually... it's Arp-Madore_2', fixed above
    result_table = Simbad.query_objects(names)
    print(len(names), len(result_table))
    #print(names, '\n', result_table['MAIN_ID'].data)
    simbad_ID = names
    for i, row in enumerate(result_table):
        simbad_ID[i] =  re.sub('\s+', ' ', row['MAIN_ID'].decode("utf-8")).strip().replace(' ','_' )
    salaris_df.insert(loc=0, column='Simbad_ID', value=simbad_ID)
    
    #check for duplicates
    for index, row in salaris_df.iterrows():
        check = salaris_df.loc[salaris_df['Simbad_ID'] == row['Simbad_ID']]
        if (len(check['Simbad_ID']) != 1):
            print('Salaris', row['Simbad_ID'], row['Name'])
            print('Check', check['Simbad_ID'].values, len(check['Simbad_ID']))
            print('')
            
    salaris_df.to_csv('Salaris2004_table1_clean.csv', index=False)

salaris_df = pd.read_csv('Salaris2004_table1_clean.csv')
salaris_df

70 70


Simbad_ID              Name   dV  err_dV  [Fe/H]  err_[Fe/H]  \
0          Cl_King_2         Cl_King_2  2.2    0.15    0.00        0.20   
1             IC_166            IC_166  1.0    0.25   -0.27        0.15   
2            NGC_752           NGC_752  0.9    0.05   -0.09        0.06   
3     Cl_Berkeley_66    Cl_Berkeley_66  2.0    0.25    0.00        0.20   
4           NGC_1193          NGC_1193  2.1    0.15   -0.35        0.11   
5         C_0311+525        C_0311+525  0.4    0.15   -0.30        0.15   
6           NGC_1245          NGC_1245  0.7    0.15    0.10        0.15   
7           NGC_1798          NGC_1798  1.0    0.15   -0.47        0.15   
8           NGC_1817          NGC_1817  0.8    0.05   -0.10        0.09   
9     Cl_Berkeley_17    Cl_Berkeley_17  2.8    0.15   -0.33        0.15   
10        Cl_King_22        Cl_King_22  2.3    0.15    0.02        0.15   
11    Cl_Berkeley_20    Cl_Berkeley_20  2.1    0.05   -0.61        0.15   
12    Cl_Berkeley_21    Cl_Berkeley_21  1.6    0.25   -0.97        0.15   
13    Cl_Berkeley_22    Cl_Berkeley_22  2.1    0.25   -0.30        0.15   
14          NGC_2141          NGC_2141  1.6    0.25   -0.26        0.15   
15          NGC_2158          NGC_2158  1.4    0.15   -0.48        0.11   
16          NGC_2194          NGC_2194  0.5    0.15    0.00        0.20   
17          NGC_2192          NGC_2192  0.6    0.15   -0.31        0.15   
18          NGC_2236          NGC_2236  0.4    0.25    0.00        0.20   
19          NGC_2243          NGC_2243  2.2    0.15   -0.48        0.06   
20        C_0634+094        C_0634+094  2.3    0.25    0.00        0.20   
21          NGC_2266          NGC_2266  0.5    0.25    0.00        0.20   
22    Cl_Berkeley_29    Cl_Berkeley_29  2.1    0.05   -0.18        0.15   
23    Cl_Berkeley_31    Cl_Berkeley_31  2.3    0.25   -0.40        0.15   
24    Cl_Berkeley_30    Cl_Berkeley_30  0.3    0.15    0.00        0.20   
25    Cl_Berkeley_32    Cl_Berkeley_32  2.4    0.15   -0.50        0.15   
26        C_0701-207        C_0701-207  1.5    0.05   -0.45        0.06   
27          NGC_2324          NGC_2324  0.3    0.25   -0.52        0.11   
28          NGC_2354          NGC_2354  0.8    0.25    0.00        0.20   
29          NGC_2355          NGC_2355  0.4    0.15   -0.07        0.15   
30          NGC_2360          NGC_2360  0.5    0.05   -0.14        0.08   
31      Cl_Haffner_6      Cl_Haffner_6  0.3    0.25    0.00        0.20   
32     Cl_Melotte_66     Cl_Melotte_66  2.3    0.15   -0.38        0.06   
33     Cl_Melotte_71     Cl_Melotte_71  0.5    0.15   -0.30        0.06   
34         ESO_368-7         ESO_368-7  2.5    0.15    0.00        0.15   
35          NGC_2506          NGC_2506  1.5    0.05   -0.42        0.09   
36        C_0816-414        C_0816-414  1.1    0.25   -0.07        0.15   
37        C_0829-385        C_0829-385  1.7    0.25    0.00        0.20   
38          NGC_2627          NGC_2627  1.6    0.15    0.00        0.20   
39          NGC_2660          NGC_2660  0.4    0.15   -0.55        0.11   
40          NGC_2849          NGC_2849  0.5    0.25    0.00        0.20   
41         ESO_92-18         ESO_92-18  2.2    0.25    0.00        0.20   
42          NGC_3680          NGC_3680  1.0    0.15    0.06        0.08   
43  Cl_Collinder_261  Cl_Collinder_261  2.6    0.15   -0.16        0.15   
44          NGC_4815          NGC_4815  1.1    0.25    0.00        0.20   
45          NGC_5822          NGC_5822  0.8    0.25    0.09        0.06   
46           IC_4651           IC_4651  1.2    0.15    0.00        0.09   
47           IC_4756           IC_4756  0.4    0.15   -0.03        0.06   
48          NGC_6802          NGC_6802  0.4    0.25    0.00        0.20   
49          NGC_6819          NGC_6819  1.7    0.15    0.15        0.09   
50          NGC_6827          NGC_6827  0.5    0.25    0.00        0.20   
51          NGC_6939          NGC_6939  1.4    0.25   -0.05        0.11   
52    Cl_Berkeley_54    Cl_Berkeley_

In [31]:
#van den Bergh (2006)
#there were two rows for Berkeley 69, with slightly different values.  I kept the first one.
if (fixVandenBergh):
    vandenbergh_df = pd.read_csv('vandenbergh2006.tsv', sep='|', header = 49)

    #fix the names
    names = vandenbergh_df['SimbadName'].values
    def representsInt(s):
        try: 
            int(s)
            return True
        except ValueError:
            return False

    for i,x in enumerate(names):
        if (x[0:2] == 'Cl'):
            names[i] = x[2:]
        if (x[0:1] == 'N' and representsInt(x[1:1])):
            names[i] = 'NGC '+x[1:]
        names[i] = names[i].strip().replace('  ',' ').replace( ' ','_' )

    vandenbergh_df['Name'] = names
    
    #add Simbad names for matching (if possible) so I reduce the duplicates 
    vandenbergh_ID = vandenbergh_df['Name']
    RA = [x*units.degree for x in vandenbergh_df['_RA[deg]']]
    Dec = [x*units.degree for x in vandenbergh_df['_Dec[deg]']]
    simbad_ID = matchToSimbad(vandenbergh_ID, RA, Dec)
    vandenbergh_df.insert(loc=0, column='Simbad_ID', value=simbad_ID)
    
    #check for duplicates
    for index, row in vandenbergh_df.iterrows():
        check = vandenbergh_df.loc[vandenbergh_df['Simbad_ID'] == row['Simbad_ID']]
        if (len(check['Simbad_ID']) != 1):
            print('van den Bergh', row['Simbad_ID'], row['Name'])
            print('Check', check['Simbad_ID'].values, len(check['Simbad_ID']))
            print('')
        
        
    vandenbergh_df.to_csv('vandenbergh2006_clean.csv', index=False)

vandenbergh_df = pd.read_csv('vandenbergh2006_clean.csv')
vandenbergh_df

Simbad_ID  Seq               Name  l[deg]  Diam[pc]  R[pc]  \
0                Trumpler_31    1        Trumpler_31       2      1.43    986   
1                   NGC_6520    2           NGC_6520       2      2.29   1577   
2                   NGC_6530    3           NGC_6530       6      5.42   1330   
3               Cl_Bochum_14    4          Bochum_14       6      0.34    578   
4                   NGC_6514    5           NGC_6514       7      6.65    816   
5                   NGC_6546    6           NGC_6546       7      3.82    938   
6                       M_21    7           NGC_6531       7      2.91   1205   
7                       M_23    8           NGC_6494       9      5.30    628   
8             Cl_Trumpler_33   10        Trumpler_33      12      2.55   1755   
9           Cl_Collinder_469   11      Collinder_469      12      1.29   1481   
10                  NGC_6603   12           NGC_6603      12      6.28   3600   
11                   IC_4725   13            IC_4725      13      5.23    620   
12                      M_18   14           NGC_6613      14      1.88   1296   
13                C_1850-204   15      Collinder_394      14      4.42    690   
14                  NGC_6618   16           NGC_6618      15      9.45   1300   
15                  NGC_6716   17           NGC_6716      15      2.30    789   
16               Cl_Blanco_1   18           Blanco_1      15      5.48    269   
17                      M_16   19           NGC_6611      16      3.05   1749   
18            Cl_Trumpler_32   20        Trumpler_32      17      2.50   1720   
19                  NGC_6604   21           NGC_6604      18      2.47   1696   
20                  NGC_6631   22           NGC_6631      19      4.54   2600   
21                  NGC_6774   23       Ruprecht_147      21      1.27    174   
22                  NGC_6649   24           NGC_6649      21      1.99   1369   
23                      M_26   25           NGC_6694      23      3.26   1600   
24                  NGC_6664   26           NGC_6664      24      4.06   1164   
25                  NGC_6683   27           NGC_6683      26      1.04   1197   
26                  NGC_6705   28           NGC_6705      27      7.10   1877   
27                C_1845-059   29            Basel_1      27      3.17   2178   
28                  NGC_6704   30           NGC_6704      28      4.33   2974   
29            Cl_Trumpler_35   31        Trumpler_35      28      1.75   1206   
30             Collinder_359   32      Collinder_359      29     17.37    249   
31                   IC_4665   33            IC_4665      30      7.17    352   
32            Cl_Berkeley_79   34        Berkeley_79      31      4.01   2300   
33            [KPR2004b]_474   35          Alessi_10      31      2.69    513   
34            Cl_Berkeley_81   36        Berkeley_81      33      4.36   3000   
35                      M_73   37           NGC_6994      35      1.62    620   
36                  NGC_6633   38           NGC_6633      36      2.19    376   
37                   IC_4756   40            IC_4756      36      5.49    484   
38                  NGC_6755   41           NGC_6755      38      5.79   1421   
39                  NGC_6756   42           NGC_6756      39      1.75   1507   
40              Cl_Alessi_19   43          Alessi_19      40     14.08    550   
41                  NGC_6709   44           NGC_6709      42      4.38   1075   
42            Cl_Berkeley_82   45        Berkeley_82      46      0.50    860   
43          Cl_Collinder_399   46      Collinder_399      54     33.42   1291   
44                  NGC_6802   47           NGC_6802      55      1.63   1124   
45                C_1950+182   48         Harvard_20      56      3.14   1540   
46                C_1956+203   49          Roslund_3      58      2.13   1467   
47                  NGC_6823   50           NGC_6823      59      3.30   1893   
48                  NGC_6830   51           NGC_68

In [32]:
#Gaia DR2 from Cantat-Gaudin+, 2018
if (fixGaia):
    gaiaDR2_df = pd.read_csv('Cantat-Gaudin2018_GaiaDR2.tsv', sep='|', header = 56)

    names = gaiaDR2_df['Name']
    names = names.str.strip()

    for index, row in  gaiaDR2_df.iterrows():
    #for i,n in enumerate(names):
        if (names[index][0:3] == "ESO"):
            names[index] = row['SimbadName'].replace(' ','_')

    gaiaDR2_df['Name'] = names

    #this already contains the Simbad name, but they are not identical to what I'm finding 
    gaiaDR2_SID = gaiaDR2_df['SimbadName'].str.replace(' ','_').replace('Name','NAME').values
    #idx = gaiaDR2_df.index[pd.isnull(gaiaDR2_df['SimbadName'])].tolist()
    #gaiaDR2_SID[idx] = names[idx]
    RA = [x + ' hour' for x in gaiaDR2_df['_RAJ2000']]
    Dec = [x + ' degree' for x in gaiaDR2_df['_DEJ2000']]
    simbad_ID = matchToSimbad(gaiaDR2_SID, RA, Dec)
    #because there was at least one bad match of Gulliver_15 to NGC 6561 (when Gulliver 15 is not in Simbad)
    #also Gulliver 7 to Ruprecht 77
    idx = gaiaDR2_df.index[pd.isnull(gaiaDR2_df['SimbadName'])].tolist()
    simbad_ID[idx] = names[idx]
    gaiaDR2_df.insert(loc=0, column='Simbad_ID', value=simbad_ID)

    #check for duplicates
    for index, row in  gaiaDR2_df.iterrows():
        check = gaiaDR2_df.loc[gaiaDR2_df['Simbad_ID'] == row['Simbad_ID']]
        if (len(check['Simbad_ID']) != 1):
            print('gaiaDR2', row['Simbad_ID'], row['Name'])
            print('Check', check['Simbad_ID'].values, len(check['Simbad_ID']))
            print('')
        
    gaiaDR2_df.to_csv('Cantat-Gaudin2018_GaiaDR2_clean.csv', index=False)

gaiaDR2_df = pd.read_csv('Cantat-Gaudin2018_GaiaDR2_clean.csv')
gaiaDR2_df#.loc[(gaiaDR2_df['Name'] == 'Collinder_258') | (gaiaDR2_df['Name'] == 'Harvard_5')]

Simbad_ID     _RAJ2000     _DEJ2000               Name  \
0                  [KPR2005]_10  03 27 28.80  +34 58 51.6            ASCC_10   
1                 [KPR2005]_101  19 13 35.76  +36 22 08.4           ASCC_101   
2                 [KPR2005]_105  19 42 11.52  +27 21 57.6           ASCC_105   
3                 [KPR2005]_107  19 48 39.36  +21 59 13.2           ASCC_107   
4                 [KPR2005]_108  19 53 13.44  +39 20 56.4           ASCC_108   
5                  [KPR2005]_11  03 32 13.44  +44 51 21.6            ASCC_11   
6                 [KPR2005]_110  20 02 58.08  +33 31 40.8           ASCC_110   
7                 [KPR2005]_111  20 11 33.84  +37 30 54.0           ASCC_111   
8                 [KPR2005]_113  21 11 43.92  +38 38 16.8           ASCC_113   
9                 [KPR2005]_114  21 39 57.60  +53 59 49.2           ASCC_114   
10                [KPR2005]_115  21 57 07.20  +51 33 28.8           ASCC_115   
11                 [KPR2005]_12  04 49 36.00  +41 44 38.4            ASCC_12   
12                [KPR2005]_123  22 41 11.76  +53 59 09.6           ASCC_123   
13                [KPR2005]_127  23 08 49.20  +64 58 26.4           ASCC_127   
14                [KPR2005]_128  23 19 47.76  +54 26 06.0           ASCC_128   
15                 [KPR2005]_13  05 13 01.20  +44 25 01.2            ASCC_13   
16                 [KPR2005]_16  05 24 47.52  +01 39 18.0            ASCC_16   
17                 [KPR2005]_19  05 27 55.68  -01 59 13.2            ASCC_19   
18                 [KPR2005]_21  05 28 42.96  +03 31 37.2            ASCC_21   
19                 [KPR2005]_23  06 20 11.28  +46 42 36.0            ASCC_23   
20                 [KPR2005]_29  06 54 17.04  -01 40 12.0            ASCC_29   
21                 [KPR2005]_30  06 57 05.04  -06 13 48.0            ASCC_30   
22                 [KPR2005]_32  07 02 51.36  -26 30 43.2            ASCC_32   
23                 [KPR2005]_41  07 46 41.76  +00 08 13.2            ASCC_41   
24                 [KPR2005]_58  10 14 37.68  -55 00 03.6            ASCC_58   
25                  [KPR2005]_6  01 47 23.04  +57 43 19.2             ASCC_6   
26                 [KPR2005]_66  11 13 28.08  -55 26 13.2            ASCC_66   
27                 [KPR2005]_67  11 41 07.20  -61 00 46.8            ASCC_67   
28                 [KPR2005]_71  12 20 07.92  -67 30 32.4            ASCC_71   
29                 [KPR2005]_73  12 37 07.44  -67 12 10.8            ASCC_73   
30                 [KPR2005]_77  14 10 46.56  -62 19 51.6            ASCC_77   
31                 [KPR2005]_79  15 18 55.44  -60 47 52.8            ASCC_79   
32                 [KPR2005]_85  16 47 24.72  -45 33 18.0            ASCC_85   
33                 [KPR2005]_87  17 02 37.92  -28 25 15.6            ASCC_87   
34                 [KPR2005]_88  17 07 32.64  -35 33 50.4            ASCC_88   
35                  [KPR2005]_9  02 46 41.04  +57 44 34.8             ASCC_9   
36                 [KPR2005]_90  17 39 06.48  -34 52 26.4            ASCC_90   
37                 [KPR2005]_97  18 37 03.12  -19 08 20.4            ASCC_97   
38                 [KPR2005]_99  18 48 40.80  -18 29 16.8            ASCC_99   
39                  Cl_Alessi_1  00 53 22.32  +49 32 09.6           Alessi_1   
40                 Cl_Alessi_10  20 04 55.92  -10 33 18.0          Alessi_10   
41                 Cl_Alessi_12  20 43 30.00  +23 52 15.6          Alessi_12   
42                 Cl_Alessi_13  03 27 02.88  -35 49 15.6          Alessi_13   
43                 Cl_Alessi_15  06 43 04.08  +01 40 19.2          Alessi_15   
44                 Cl_Alessi_17  07 35 24.72  -15 05 52.8          Alessi_17   
45                 Cl_Alessi_18  07 37 10.80  -26 23 09.6          Alessi_18   
46                 Cl_Alessi_19  18 18 57.84  +12 18 39.6          Alessi_19   
47                  Cl_Alessi_2  04 46 24.48  +55 11 56.4           Alessi_2   
48                 [KPR2004b]_4  00 10 22.32  +58 44 31.2          Alessi_20   
49                 Cl_

In [33]:
#lynga catalo: https://heasarc.gsfc.nasa.gov/W3Browse/star-catalog/lyngaclust.html
if (fixLynga):
    lynga_df = pd.read_csv('lyngaCat.txt',sep='|')

    #fix the column names
    lynga_df.rename(columns=lambda x: x.strip(), inplace=True)

    #fix all the cells
    lynga_df = lynga_df.apply(lambda x: x.str.strip() if x.dtype == "object" else x)
    lynga_df.replace(r'^\s*$', np.nan, regex=True, inplace=True)

    #take only the first entries for each name (some have multiple lines
    lynga_df = lynga_df.loc[pd.notna(lynga_df['Name'].str.strip())]

    #fix capitalization in the names!
    names = lynga_df['Name'].values
    for i,n in enumerate(names):
        if ((n[0:3] != 'NGC') and (n[0:2] != 'IC')):
            p1 = n.find(' ')
            n = n[0] + n[1:p1].lower() + n[p1:]

        if (n[0:9] == 'Vdb-hagen'):
            n = 'vdBergh-Hagen' + n[9:]

        if (n[0:10] == 'Hav-moffat'):
            n = 'Havlen-Moffat' + n[10:]

        if (n[0:7] == 'Vdbergh'):
            n = 'vdBergh' + n[7:]

        if (n[0:8] == 'Dol-dzim'):
            n = 'Dol-Dzim' + n[8:]

        if (n == 'Sigma ORI'):
            n = 'Sigma Ori'

        names[i] = n.replace(' ','_')

    lynga_df['Name'] = names

    #print(lynga_df.loc[lynga_df['Name'] == 'NGC_2579'])
    
    #remove the "Unnamed" columns
    lynga_df = lynga_df.loc[:, ~lynga_df.columns.str.contains('^Unnamed')]
    
    #add Simbad names for matching (if possible) so I reduce the duplicates 
    lynga_ID = lynga_df['Name']
    RA = [x*units.degree for x in lynga_df['ra']]
    Dec = [x*units.degree for x in lynga_df['dec']]
    simbad_ID = matchToSimbad(lynga_ID, RA, Dec)
    lynga_df.insert(loc=0, column='Simbad_ID', value=simbad_ID)
    
    #check for duplicates
    for index, row in  lynga_df.iterrows():
        check = lynga_df.loc[lynga_df['Simbad_ID'] == row['Simbad_ID']]
        if (len(check['Simbad_ID']) != 1):
            print('lynga', row['Simbad_ID'], row['Name'])
            print('Check', check['Simbad_ID'].values, len(check['Simbad_ID']))
            print('')
        
    lynga_df.to_csv('lyngaCat_clean.csv', index=False)
    
lynga_df = pd.read_csv('lyngaCat_clean.csv')
lynga_df

Simbad_ID               Name         ra       dec  \
0             Cl_Berkeley_59        Berkeley_59    0.64425  67.37840   
1            Cl_Berkeley_104       Berkeley_104    0.87085  63.59506   
2                Cl_Blanco_1           Blanco_1    1.06343 -29.92162   
3                   Stock_19           Stock_19    1.09607  56.02838   
4                  Czernik_1          Czernik_1    1.92972  61.41163   
5              Cl_Berkeley_1         Berkeley_1    2.40822  60.42822   
6                 C_0007+609            King_13    2.53490  61.21153   
7             Cl_Berkeley_60        Berkeley_60    4.42607  60.96103   
8                 C_0019+641             King_1    5.49230  64.39395   
9              Cl_Berkeley_2         Berkeley_2    6.31620  60.39356   
10                   NGC_103            NGC_103    6.31822  61.34356   
11                   NGC_110            NGC_110    6.83291  71.39330   
12                   NGC_129            NGC_129    7.47555  60.22625   
13                  Stock_21           Stock_21    7.52080  57.97623   
14                   NGC_133            NGC_133    7.81211  63.35938   
15                   NGC_136            NGC_136    7.88239  61.52600   
16                C_0029+628            King_14    7.96291  63.15929   
17                Cl_King_15            King_15    8.23648  61.85911   
18                   NGC_146            NGC_146    8.26620  63.29242   
19               Cl_Stock_24           Stock_24    9.92686  61.95787   
20                   NGC_189            NGC_189    9.89852  61.07456   
21                   NGC_225            NGC_225   10.85949  61.79042   
22                C_0040+639            King_16   10.92026  64.19037   
23                C_0040+598          Czernik_2   10.92900  60.15702   
24                   NGC_188            NGC_188   11.09356  85.34044   
25             Cl_Berkeley_4         Berkeley_4   11.37576  64.40662   
26            Cl_Berkeley_61        Berkeley_61   12.12461  67.23925   
27                Dolidze_13         Dolidze_13   12.51048  64.13886   
28                 Cl_King_2             King_2   12.76134  58.18858   
29            Cl_Berkeley_62        Berkeley_62   15.26081  63.95242   
30                C_0100+625          Czernik_3   15.78349  62.80175   
31                   NGC_366            NGC_366   16.61238  62.23399   
32                   NGC_381            NGC_381   17.08751  61.58334   
33                   Stock_3            Stock_3   18.07584  62.33193   
34                  Basel_10           Basel_10   34.69319  58.31347   
35                   NGC_433            NGC_433   18.81789  60.13081   
36                   NGC_436            NGC_436   18.91085  58.81399   
37                   NGC_457            NGC_457   19.76443  58.32931   
38               Cl_Stock_20           Stock_20    6.22025  62.64361   
39                   NGC_559            NGC_559   22.37134  63.30823   
40                   NGC_581            NGC_581   23.30754  60.70648   
41              Cl_Czernik_4          Czernik_4   23.84274  61.43880   
42                C_0132+610         Trumpler_1   23.91710  61.28866   
43                   NGC_609            NGC_609   24.30088  64.55461   
44                   NGC_637            NGC_637   25.73305  64.00172   
45                   NGC_657            NGC_657   25.94172  55.86788   
46                   NGC_654            NGC_654   26.01434  61.88445   
47                   NGC_659            NGC_659   26.05401  60.70102   
48                   NGC_663            NGC_663   26.51248  61.25006   
49             Cl_Berkeley_5         Berkeley_5   26.95745  62.93245   
50             Collinder_463      Collinder_463   27.09502  71.94897   
51              Collinder_21       Collinder_21   27.53066  27.24767   
52             Cl_Berkeley_6         Berkeley_6   27.79594  61.08059   
53                    IC_166             IC_166   28.13086  61.82985   
54                C_0149+568            Stock_4   28.18981 

In [34]:
#mwsc + webda
mwsc_webda_df = mwsc_df.join(webda_df.set_index('Simbad_ID'),
                            on='Simbad_ID',how='outer', lsuffix='_mwsc', rsuffix='_webda')
      
# + piskunov
mwsc_webda_piskunov_df = mwsc_webda_df.join(piskunov_df.set_index('Simbad_ID'), 
                            on='Simbad_ID', how='outer', rsuffix='_piskunov')

# + kharchenko
mwsc_webda_piskunov_kharchenko_df = mwsc_webda_piskunov_df.join(kharchenko_df.set_index('Simbad_ID'), 
                            on='Simbad_ID', how='outer', rsuffix='_kharchenko')

# + Salaris
mwsc_webda_piskunov_kharchenko_salaris_df = mwsc_webda_piskunov_kharchenko_df.join(salaris_df.set_index('Simbad_ID'), 
                            on='Simbad_ID', how='outer', rsuffix='_salaris')

# + vandenberg
mwsc_webda_piskunov_kharchenko_salaris_vandenbergh_df = mwsc_webda_piskunov_kharchenko_salaris_df.join(
                            vandenbergh_df.set_index('Simbad_ID'), 
                            on='Simbad_ID', how='outer', rsuffix='_vandenbergh')


# + Gaia
mwsc_webda_piskunov_kharchenko_salaris_vandenbergh_gaia_df = mwsc_webda_piskunov_kharchenko_salaris_vandenbergh_df.join(
                            gaiaDR2_df.set_index('Simbad_ID'), 
                            on='Simbad_ID', how='outer', rsuffix='_GaiaDR2')

# + Lynga
mwsc_webda_piskunov_kharchenko_salaris_vandenbergh_gaia_lynga_df = mwsc_webda_piskunov_kharchenko_salaris_vandenbergh_gaia_df.join(
                            lynga_df.set_index('Simbad_ID'), 
                            on='Simbad_ID', how='outer', rsuffix='_lynga')

#rename
OCs = mwsc_webda_piskunov_kharchenko_salaris_vandenbergh_gaia_lynga_df.copy()

print(len(OCs.loc[pd.isnull(OCs['Simbad_ID'])]))

#reindex
OCs = OCs.reset_index(drop=True)

#if there are NaN rows; drop them
idx = OCs.index[pd.isnull(OCs['Simbad_ID'])]
OCs.drop(idx, inplace=True)

#reindex
OCs = OCs.reset_index(drop=True)


print(len(mwsc_df), len(webda_df), len(piskunov_df), len(kharchenko_df), len(salaris_df), len(vandenbergh_df),
     len(gaiaDR2_df), len(lynga_df), len(mwsc_webda_piskunov_kharchenko_salaris_vandenbergh_gaia_df),
      len(mwsc_webda_piskunov_kharchenko_salaris_vandenbergh_gaia_lynga_df), len(OCs))

print(OCs.columns.values)

#dump to a file
OCs.to_csv('OCcompiled.csv', index=False)


0
2908 936 650 3005 70 595 1228 1080 3496 3689 3689
['Simbad_ID' 'Name_mwsc' 'broad_type' 'cluster_status' 'ra' 'dec' 'lii'
 'bii' 'core_radius' 'central_radius' 'cluster_radius' 'pm_ra' 'pm_dec'
 'pm_tot_error' 'rad_vel' 'rad_vel_error' 'num_rad_vel_stars'
 'num_core_stars' 'num_central_stars' 'num_cluster_stars' 'distance'
 'e_bv' 'distance_modulus' 'e_jk' 'e_jh' 'delta_h' 'log_age'
 'log_age_error' 'num_log_age_stars' 'king_core_radius'
 'king_core_radius_error' 'king_tidal_radius' 'king_tidal_radius_error'
 'king_norm_factor' 'king_norm_factor_error' 'reference_code'
 'cluster_type' 'metallicity' 'metallicity_error' 'num_metallicity_stars'
 'comments' 'class' 'Name_webda' 'RA_2000' 'Dec_2000' 'l' 'b' 'Dist' 'Mod'
 'EB-V' 'Age' 'ST' 'Z' 'Diam' 'Fe/H' 'MRV' 'pm RA' 'pm Dec' 'Measures'
 'Stars' 'COCD' 'Name' 'GLON[deg]' 'GLAT[deg]' 'DistMod' 'E(B-V)'
 'Dist[pc]' 'logt[yr]' 'rt[pc]' 'e_rt[pc]' 'logM[MSun]' 'e_logM[MSun]'
 'rtA[pc]' 'e_rtA[pc]' 'logMA[MSun]' 'e_logMA[MSun]' 'MWSC'
 'Nam

In [35]:
#a quick check to make sure that items matched up
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
#print(OCs.loc[OCs['Simbad_ID'] == 'C_1440+697'].iloc[0])
print(OCs.loc[OCs['Simbad_ID'] == 'NGC_2682'].iloc[0])

Simbad_ID                                                           NGC_2682
Name_mwsc                                                           NGC_2682
broad_type                                                                  
cluster_status                                                              
ra                                                                  08 51 23
dec                                                                 +11 48.9
lii                                                                  215.691
bii                                                                   31.923
core_radius                                                              0.1
central_radius                                                          0.55
cluster_radius                                                          1.03
pm_ra                                                                  -7.31
pm_dec                                                                 -5.92

In [36]:
#check for duplicates (by definition there should be none)
for index, row in  OCs.iterrows():
    check = OCs.loc[OCs['Simbad_ID'] == row['Simbad_ID']]
    if (len(check['Simbad_ID']) != 1):
        print('OCS', row['Simbad_ID'], row['Name'])
        print('Check', check['Simbad_ID'].values, len(check['Simbad_ID']))
        print('')

OCS [BDS2003]_73 nan
Check ['[BDS2003]_73' '[BDS2003]_73'] 2

OCS [BDS2003]_73 nan
Check ['[BDS2003]_73' '[BDS2003]_73'] 2



In [37]:
check = OCs.loc[OCs['Simbad_ID'].str.contains('Berkeley_69')]
print(len(check['Simbad_ID']))


1


In [38]:
check = OCs.loc[OCs['Simbad_ID'] == '[BDS2003]_73']
#check = mwsc_df.loc[mwsc_df['Simbad_ID'] == '[BDS2003]_73']
#check = mwsc_df.loc[mwsc_df['Name']== 'BDSB_73']
#print(len(check['Simbad_ID']))
check

Simbad_ID Name_mwsc  broad_type  cluster_status        ra       dec  \
2202  [BDS2003]_73   BDSB_73                              05 41 33  +35 51.7   
2203  [BDS2003]_73   BDSB_73                              05 41 33  +35 51.7   

         lii    bii  core_radius  central_radius  cluster_radius  pm_ra  \
2202  173.65  2.899        0.025             0.1           0.185   2.52   
2203  173.65  2.899        0.025             0.1           0.185   2.52   

      pm_dec  pm_tot_error   rad_vel  rad_vel_error  num_rad_vel_stars  \
2202    -4.9          0.45    -13.41                                 1   
2203    -4.9          0.45    -13.41                                 1   

      num_core_stars  num_central_stars  num_cluster_stars  distance   e_bv  \
2202             5.0               39.0              115.0    1110.0  0.541   
2203             5.0               39.0              115.0    1110.0  0.541   

      distance_modulus  e_jk   e_jh  delta_h  log_age  log_age_error  \
2202            10.401  0.26  0.173      0.0    8.875                  
2203            10.401  0.26  0.173      0.0    8.875                  

      num_log_age_stars  king_core_radius  king_core_radius_error  \
2202                                 1.92                    0.68   
2203                                 1.92                    0.68   

      king_tidal_radius  king_tidal_radius_error  king_norm_factor  \
2202               7.12                     2.02              4.32   
2203               7.12                     2.02              4.32   

      king_norm_factor_error  reference_code  cluster_type  metallicity  \
2202                    1.14  FPRO                                        
2203                    1.14  FPRO                                        

      metallicity_error  num_metallicity_stars  \
2202                                       0.0   
2203                                       0.0   

                                               comments  \
2202  Overlaps with corona of Sh2_235, BDSB_72, and ...   
2203  Overlaps with corona of Sh2_235, BDSB_72, and ...   

                                                  class Name_webda RA_2000  \
2202                                    OPEN STAR CL...        NaN     NaN   
2203                                    OPEN STAR CL...        NaN     NaN   

     Dec_2000   l   b  Dist  Mod  EB-V  Age   ST   Z  Diam  Fe/H  MRV  pm RA  \
2202      NaN NaN NaN   NaN  NaN   NaN  NaN  NaN NaN   NaN   NaN  NaN    NaN   
2203      NaN NaN NaN   NaN  NaN   NaN  NaN  NaN NaN   NaN   NaN  NaN    NaN   

      pm Dec  Measures  Stars  COCD Name  GLON[deg]  GLAT[deg]  DistMod  \
2202     NaN       NaN    NaN   NaN  NaN        NaN        NaN      NaN   
2203     NaN       NaN    NaN   NaN  NaN        NaN        NaN      NaN   

      E(B-V)  Dist[pc]  logt[yr]  rt[pc]  e_rt[pc]  logM[MSun]  e_logM[MSun]  \
2202     NaN       NaN       NaN     NaN       NaN         NaN           NaN   
2203     NaN       NaN       NaN     NaN       NaN         NaN           NaN   

      rtA[pc]  e_rtA[pc]  logMA[MSun]  e_logMA[MSun]   MWSC Name_kharchenko  \
2202      NaN        NaN          NaN            NaN  631.0        Sh2_235B   
2203      NaN        NaN          NaN            NaN  639.0         BDSB_73   

     Type  n_Type  RA[hr]  Dec[deg]  GLON[deg]_kharchenko  \
2202   no     NaN  5.6815    35.707               173.706   
2203  NaN     NaN  5.6925    35.861               173.645   

      GLAT[deg]_kharchenko  r0[deg]  r1[deg]  r2[deg]  pmRA[mas/yr]  \
2202                 2.697    0.020    0.095    0.140          1.45   
2203                 2.892    0.025    0.100    0.185          2.52   

      pmDec[mas/yr]  e_pm[mas/yr]  RV[km/s]  e_RV[km/s]  n_RV[km/s]  N1sr0  \
2202          -4.66          0.56     -8.86         0.3         2.0    1.0   
2203          -4.90          0.45    -13.41         NaN         1.0    5.0   

      N1sr1  N1sr2   d[pc]  E(B-V)_kharchenko  appDistMod[mag]  E(J-Ks)  \
2

In [39]:
check = OCs.loc[pd.isna(OCs['Simbad_ID'])]
check

Empty DataFrame
Columns: [Simbad_ID, Name_mwsc, broad_type, cluster_status, ra, dec, lii, bii, core_radius, central_radius, cluster_radius, pm_ra, pm_dec, pm_tot_error, rad_vel, rad_vel_error, num_rad_vel_stars, num_core_stars, num_central_stars, num_cluster_stars, distance, e_bv, distance_modulus, e_jk, e_jh, delta_h, log_age, log_age_error, num_log_age_stars, king_core_radius, king_core_radius_error, king_tidal_radius, king_tidal_radius_error, king_norm_factor, king_norm_factor_error, reference_code, cluster_type, metallicity, metallicity_error, num_metallicity_stars, comments, class, Name_webda, RA_2000, Dec_2000, l, b, Dist, Mod, EB-V, Age, ST, Z, Diam, Fe/H, MRV, pm RA, pm Dec, Measures, Stars, COCD, Name, GLON[deg], GLAT[deg], DistMod, E(B-V), Dist[pc], logt[yr], rt[pc], e_rt[pc], logM[MSun], e_logM[MSun], rtA[pc], e_rtA[pc], logMA[MSun], e_logMA[MSun], MWSC, Name_kharchenko, Type, n_Type, RA[hr], Dec[deg], GLON[deg]_kharchenko, GLAT[deg]_kharchenko, r0[deg], r1[deg], r2[deg], pmRA[mas/yr], pmDec[mas/yr], e_pm[mas/yr], RV[km/s], e_RV[km/s], n_RV[km/s], N1sr0, N1sr1, N1sr2, d[pc], E(B-V)_kharchenko, appDistMod[mag], E(J-Ks), ...]
Index: []

## Check for duplicates in RA and Dec

In [40]:
def getCoord(row):

    if (pd.notna(row['_RAJ2000']) and pd.notna(row['_DEJ2000'])):
        return SkyCoord(ra=row['_RAJ2000']+' hours', dec=row['_DEJ2000']+' degree', frame='icrs')
    
    elif (pd.notna(row['ra']) and pd.notna(row['dec'])):
        return SkyCoord(ra=row['ra']+' hours', dec=row['dec']+' degree', frame='icrs')
        
    elif (pd.notna(row['ra_lynga']) and pd.notna(row['dec_lynga'])):
        return SkyCoord(ra=row['ra_lynga']*units.degree, dec=row['dec_lynga']*units.degree, frame='icrs')
    
    elif (pd.notna(row['RA_2000']) and pd.notna(row['Dec_2000'])):
        return SkyCoord(ra=row['RA_2000']+' hours', dec=row['Dec_2000']+' degree', frame='icrs')
        
    elif (pd.notna(row['RA[hr]']) and pd.notna(row['Dec[deg]'])):
        return SkyCoord(ra=row['RA[hr]']*units.hourangle, dec=row['Dec[deg]']*units.degree, frame='icrs')
        
    elif (pd.notna(row['_RA[deg]']) and pd.notna(row['_Dec[deg]'])):
        return SkyCoord(ra=row['_Dec[deg]']*units.degree, dec=row['_Dec[deg]']*units.degree, frame='icrs')
        
    elif (pd.notna(row['GLON[deg]']) and pd.notna(row['GLAT[deg]'])):
        return SkyCoord(l=row['GLON[deg]']*units.degree, b=row['GLAT[deg]']*units.degree, frame='galactic').icrs

    elif (pd.notna(row['l']) and pd.notna(row['b'])):
        return SkyCoord(l=row['l']*units.degree, b=row['b']*units.degree, frame='galactic').icrs
    
    else:
        print('NO RA, Dec : ', row['Simbad_ID'])
        return False

In [41]:
#first get the coordinates in lists
RA = []
Dec = []
for index, row in OCs.iterrows():
    #RA and Dec
    c = getCoord(row)
    if (c):
        RA.append(c.ra.degree)
        Dec.append(c.dec.degree)

catalog = SkyCoord(ra = RA*units.degree, dec = Dec*units.degree)

In [42]:
#now match to the full catalog to see if there are duplicates
#I think these are OK overlaps (really different clusters)
#!!! OVERLAP NGC_3590 Hogg_12 [0.46110687] 253 2967
#!!! OVERLAP C_0925-549 Ruprecht_77 [0.90177733] 473 3360
#!!! OVERLAP NGC_6997 NGC_6996 [0.91921481] 3238 3250
#!!! OVERLAP Cl_Platais_8 NAME_HIP_67014_Cluster [0.44914403] 3260 3266
#!!! OVERLAP AH03_J0822-36.4 NGC_2579 [0.97738812] 888 3046 #not sure about this; NGC 2579 is labelled as HII region in Simbad
#!!! OVERLAP Cl_Pismis_24 NGC_6357 [0.97546562] 3134 3347 #nto sure about this; NGC 6357 is labelled as HII region in Simbad


#need to fix:
#!!! OVERLAP [BDS2003]_73 [BDS2003]_73 [6.47828804e-13] 2202 2203

max_sep = 1.0 * units.arcmin
nover = 0
for index, row in OCs.iterrows():
    c = getCoord(row)
    idx, d2d, d3d = c.match_to_catalog_sky(catalog, nthneighbor=2) #first neighbor is itself
    #print(index, row['Name'], OCs.iloc[int(idx)]['Name'], d2d.degree)
    if (d2d < max_sep and idx != index):
        print('!!! OVERLAP',row['Simbad_ID'], OCs.iloc[int(idx)]['Simbad_ID'], d2d.arcminute, index, idx)
        nover += 1

#this should be 12
print(nover)
        


!!! OVERLAP NGC_3590 Hogg_12 [0.46110687] 253 2993
!!! OVERLAP C_0925-549 Ruprecht_77 [0.90177733] 473 3483
!!! OVERLAP C_0847-465 Ruprecht_71 [0.90420297] 676 3482
!!! OVERLAP AH03_J0822-36.4 NGC_2579 [0.97738812] 888 3094
!!! OVERLAP NGC_6494 M_23 [0.89772001] 1300 3007
!!! OVERLAP C_0747-171 Ruprecht_37 [0.96929315] 1331 3550
!!! OVERLAP NGC_2323 M_50 [0.41511329] 1518 3465
!!! OVERLAP Basel_8 Cl_Basel_8 [0.3] 1777 3365
!!! OVERLAP Czernik_18 C_0424+308 [0.59099504] 2117 3368
!!! OVERLAP [BDS2003]_73 [BDS2003]_73 [6.47828804e-13] 2203 2202
!!! OVERLAP NAME_Alessi_Teutsch_3 Name_Cl_Alessi_Teutsch_3 [0.9250396] 2970 3355
!!! OVERLAP Hogg_12 NGC_3590 [0.46110687] 2993 253
!!! OVERLAP M_23 NGC_6494 [0.89772001] 3007 1300
!!! OVERLAP NGC_2579 AH03_J0822-36.4 [0.97738812] 3094 888
!!! OVERLAP NGC_6997 NGC_6996 [0.91921481] 3289 3303
!!! OVERLAP NGC_6996 NGC_6997 [0.91921481] 3303 3289
!!! OVERLAP Name_Cl_Alessi_Teutsch_3 NAME_Alessi_Teutsch_3 [0.9250396] 3355 2970
!!! OVERLAP Cl_Basel_8 B

In [22]:
print(OCs.columns.values)

['Simbad_ID' 'Name_mwsc' 'broad_type' 'cluster_status' 'ra' 'dec' 'lii'
 'bii' 'core_radius' 'central_radius' 'cluster_radius' 'pm_ra' 'pm_dec'
 'pm_tot_error' 'rad_vel' 'rad_vel_error' 'num_rad_vel_stars'
 'num_core_stars' 'num_central_stars' 'num_cluster_stars' 'distance'
 'e_bv' 'distance_modulus' 'e_jk' 'e_jh' 'delta_h' 'log_age'
 'log_age_error' 'num_log_age_stars' 'king_core_radius'
 'king_core_radius_error' 'king_tidal_radius' 'king_tidal_radius_error'
 'king_norm_factor' 'king_norm_factor_error' 'reference_code'
 'cluster_type' 'metallicity' 'metallicity_error' 'num_metallicity_stars'
 'comments' 'class' 'Name_webda' 'RA_2000' 'Dec_2000' 'l' 'b' 'Dist' 'Mod'
 'EB-V' 'Age' 'ST' 'Z' 'Diam' 'Fe/H' 'MRV' 'pm RA' 'pm Dec' 'Measures'
 'Stars' 'COCD' 'Name' 'GLON[deg]' 'GLAT[deg]' 'DistMod' 'E(B-V)'
 'Dist[pc]' 'logt[yr]' 'rt[pc]' 'e_rt[pc]' 'logM[MSun]' 'e_logM[MSun]'
 'rtA[pc]' 'e_rtA[pc]' 'logMA[MSun]' 'e_logMA[MSun]' 'MWSC'
 'Name_kharchenko' 'Type' 'n_Type' 'RA[hr]' 'Dec[deg]'
 '

# Make a plot of the age distribution and mass distribution

### First check how many have both

In [23]:
def getMass(row, mm = 0.5):
    #take a mean if there are more than 1
    masses = []
    if (pd.notna(row['num_cluster_stars'])):
        masses.append(row['num_cluster_stars']*mm)
        
    if (pd.notna(row['Nstars'])):
        masses.append(row['Nstars']*mm)    

    if (pd.notna(row['Stars'])):
        masses.append(row['Stars']*mm)    
        
    if (pd.notna(row['ly_member_stars'])):
        if row['ly_member_stars'].isnumeric():
            masses.append(float(row['ly_member_stars'])*mm)
        
    if (pd.notna(row['N1sr2'])):
        masses.append(row['N1sr2']*mm)    
        
    if (pd.notna(row['logM[MSun]'])):
        masses.append(10.**row['logM[MSun]'])
        
    if (pd.notna(row['logMA[MSun]'])):
        masses.append(10.**row['logMA[MSun]'])
        

    if (len(masses) > 0):
        masses = np.array(masses)
        return (np.mean(masses), np.std(masses)/(len(masses))**0.5)
    else:
        print('NO MASS', row['Name'])
        return (np.nan, np.nan)

mass = []
for index, row in OCs.iterrows():
    m,em  = getMass(row)
    if (~np.isnan(m)):
        mass.append(m)
        

# hasAge = OCs.loc[(pd.notna(OCs['Age'])) | 
#                  (pd.notna(OCs['log_age'])) |
#                  (pd.notna(OCs['logt[yr]'])) |
#                  (pd.notna(OCs['logt[yr]_kharchenko'])) |
#                  (pd.notna(OCs['logt'])) |
#                  (pd.notna(OCs['logt_vandenbergh'])) |
#                  (pd.notna(OCs['t[Gyr]']))
#                  ]
# hasBoth = OCs.loc[( 
#          (pd.notna(OCs['logM[MSun]'])) |
#          (pd.notna(OCs['num_cluster_stars'])) |
#          (pd.notna(OCs['Stars'])) | 
#          (pd.notna(OCs['logMA[MSun]'])) |
#          (pd.notna(OCs['N1sr0'])) |
#          (pd.notna(OCs['N1sr1'])) |
#          (pd.notna(OCs['N1sr2'])) 
#     ) & (
#         (pd.notna(OCs['Age'])) | 
#         (pd.notna(OCs['log_age'])) |
#         (pd.notna(OCs['logt[yr]'])) |
#         (pd.notna(OCs['logt[yr]_kharchenko'])) |
#         (pd.notna(OCs['logt'])) |
#         (pd.notna(OCs['logt_vandenbergh'])) |
#         (pd.notna(OCs['t[Gyr]']))
#     )]
print(len(OCs), len(mass))
#print(mass)

AttributeError: 'float' object has no attribute 'isnumeric'

In [ ]:
noAge = OCs.loc[(pd.isnull(OCs['Age'])) &
                 (pd.isnull(OCs['log_age'])) &
                 (pd.isnull(OCs['logt[yr]'])) &
                 (pd.isnull(OCs['logt[yr]_kharchenko'])) &
                 (pd.isnull(OCs['logt'])) &
                 (pd.isnull(OCs['logt_vandenbergh'])) &
                 (pd.isnull(OCs['t[Gyr]']))
                 ]
noAge

In [ ]:
#Add a column to estimate the mass from the number of stars? (or vice versa) 
#This would require an estimate of the mean mass, which depends on age

#as a test, just assume <m>=0.5
meanM = 0.5

logMass = []
logAge = []
name = []
for index, row in  hasBoth.iterrows():
    name.append(row['name'])
    
    #age
#     (pd.notnull(OCs['Age'])) | 
#                  (pd.notnull(OCs['log_age'])) |
#                  (pd.notnull(OCs['logt[yr]'])) |
#                  (pd.notnull(OCs['logt[yr]_kharchenko'])) |
#                  (pd.notnull(OCs['logt'])) |
#                  (pd.notnull(OCs['logt_vandenbergh'])) |
#                  (pd.notnull(OCs['t[Gyr]']))
                 
                
    if (pd.notnull(row['log_age'])): #MWSC
        logAge.append(row['log_age'])
    elif (pd.notnull(row['logt'])): #Solaris
        logAge.append(row['logt'])
    elif (pd.notnull(row['log(t[yr])K'])): #Kharchenko
        logAge.append(row['log(t[yr])K'])
    elif (pd.notnull(row['Age'])): #WEBDA
        logAge.append(np.log10(row['Age']))

    #mass
#          (pd.notnull(OCs['logM[MSun]'])) |
#          (pd.notnull(OCs['num_cluster_stars'])) |
#          (pd.notnull(OCs['Stars'])) | 
#          (pd.notnull(OCs['logMA[MSun]'])) |
#          (pd.notnull(OCs['N1sr0'])) |
#          (pd.notnull(OCs['N1sr1'])) |
#          (pd.notnull(OCs['N1sr2'])) 
        
    if (pd.notnull(row['logM[Msun]'])): #Piskunov
        logMass.append(row['logM[Msun]'])    
    elif (pd.notnull(row['num_cluster_stars'])): #MWSC <-- NEED TO FIX THIS 
        logMass.append(np.log10(row['num_cluster_stars']*meanM))
        
print(len(name), len(logAge), len(logMass))

### Make a few plots

In [ ]:
f,(ax1, ax2) = plt.subplots(1,2)

ax1.hist(logAge, bins=40, density=True)
ax1.set_xlabel('log(Age [yr?])')
ax1.set_yscale('log')

ax2.hist(logMass, bins=40, density=True)
ax2.set_xlabel('log(Mass [Msun])')
ax2.set_yscale('log')


### As if I'm only reading from the file

In [ ]:
df = pd.read_csv("OCcompiled_hasAgeMass.csv")

data = np.vstack((df['logAge'].values, df['logMass'].values))
KDE = gaussian_kde(data)
sample = KDE.resample(size=int(1e5))

nbins = 40

f,(ax1, ax2) = plt.subplots(1,2)
ax1.hist(df['logAge'].values, bins=nbins, density=True)
ax1.hist(sample[0,:], bins=nbins, density=True, histtype='step')
ax1.set_xlabel('log(Age [yr?])')
ax1.set_yscale('log')

ax2.hist(df['logMass'].values, bins=nbins, density=True)
ax2.hist(sample[1,:], bins=nbins, density=True, histtype='step')
ax2.set_xlabel('log(Mass [Msun])')
ax2.set_yscale('log')

lt = 5
lm = 2
values = np.vstack([lt, lm])
print(KDE(values))
#NOTE: the age KDE seems to be missing the edges.  Maybe I should set those to zero automatically?

### Make a smaller file that has everything we need for the EBLSST code

Name, RA, Dec, dist[kpc], rh[pc], mass[Msun], Age[Myr], Z, sigma_v[km/s]

In [ ]:
df = pd.read_csv("OCcompiled.csv")


name = []
RA = []
Dec = []

logMass = []
logAge = []
for index, row in df.iterrows():
    name.append(row['name'])
    
    #RA
    if (pd.notnull(row['ra'])):
        RA.append(row['ra'])
    elif (pd.notnull(row['RA_2000'])):
        RA.append(row['RA_2000'])
    else:
        print('NO RA', row['name'])
        #print('\nNO RA', row)
     
    #Dec
    Dec.append(row['dec'])
    
    #age
    if (pd.notnull(row['log_age'])): #MWSC
        logAge.append(row['log_age'])
    elif (pd.notnull(row['logt'])): #Solaris
        logAge.append(row['logt'])
    elif (pd.notnull(row['log(t[yr])K'])): #Kharchenko
        logAge.append(row['log(t[yr])K'])
    elif (pd.notnull(row['Age'])): #WEBDA
        logAge.append(np.log10(row['Age']))

print(len(name),len(RA))